# Computer Vision Nanodegree

## Project: Image Captioning

---

In this notebook, you will train your CNN-RNN model.  

You are welcome and encouraged to try out many different architectures and hyperparameters when searching for a good model.

This does have the potential to make the project quite messy!  Before submitting your project, make sure that you clean up:
- the code you write in this notebook.  The notebook should describe how to train a single CNN-RNN architecture, corresponding to your final choice of hyperparameters.  You should structure the notebook so that the reviewer can replicate your results by running the code in this notebook.  
- the output of the code cell in **Step 2**.  The output should show the output obtained when training the model from scratch.

This notebook **will be graded**.  

Feel free to use the links below to navigate the notebook:
- [Step 1](#step1): Training Setup
- [Step 2](#step2): Train your Model
- [Step 3](#step3): (Optional) Validate your Model

<a id='step1'></a>
## Step 1: Training Setup

In this step of the notebook, you will customize the training of your CNN-RNN model by specifying hyperparameters and setting other options that are important to the training procedure.  The values you set now will be used when training your model in **Step 2** below.

You should only amend blocks of code that are preceded by a `TODO` statement.  **Any code blocks that are not preceded by a `TODO` statement should not be modified**.

### Task #1

Begin by setting the following variables:
- `batch_size` - the batch size of each training batch.  It is the number of image-caption pairs used to amend the model weights in each training step. 
- `vocab_threshold` - the minimum word count threshold.  Note that a larger threshold will result in a smaller vocabulary, whereas a smaller threshold will include rarer words and result in a larger vocabulary.  
- `vocab_from_file` - a Boolean that decides whether to load the vocabulary from file. 
- `embed_size` - the dimensionality of the image and word embeddings.  
- `hidden_size` - the number of features in the hidden state of the RNN decoder.  
- `num_epochs` - the number of epochs to train the model.  We recommend that you set `num_epochs=3`, but feel free to increase or decrease this number as you wish.  [This paper](https://arxiv.org/pdf/1502.03044.pdf) trained a captioning model on a single state-of-the-art GPU for 3 days, but you'll soon see that you can get reasonable results in a matter of a few hours!  (_But of course, if you want your model to compete with current research, you will have to train for much longer._)
- `save_every` - determines how often to save the model weights.  We recommend that you set `save_every=1`, to save the model weights after each epoch.  This way, after the `i`th epoch, the encoder and decoder weights will be saved in the `models/` folder as `encoder-i.pkl` and `decoder-i.pkl`, respectively.
- `print_every` - determines how often to print the batch loss to the Jupyter notebook while training.  Note that you **will not** observe a monotonic decrease in the loss function while training - this is perfectly fine and completely expected!  You are encouraged to keep this at its default value of `100` to avoid clogging the notebook, but feel free to change it.
- `log_file` - the name of the text file containing - for every step - how the loss and perplexity evolved during training.

If you're not sure where to begin to set some of the values above, you can peruse [this paper](https://arxiv.org/pdf/1502.03044.pdf) and [this paper](https://arxiv.org/pdf/1411.4555.pdf) for useful guidance!  **To avoid spending too long on this notebook**, you are encouraged to consult these suggested research papers to obtain a strong initial guess for which hyperparameters are likely to work best.  Then, train a single model, and proceed to the next notebook (**3_Inference.ipynb**).  If you are unhappy with your performance, you can return to this notebook to tweak the hyperparameters (and/or the architecture in **model.py**) and re-train your model.

### Question 1

**Question:** Describe your CNN-RNN architecture in detail.  With this architecture in mind, how did you select the values of the variables in Task 1?  If you consulted a research paper detailing a successful implementation of an image captioning model, please provide the reference.

**Answer:** It is straight forward like in the paper "Show and Tell: A Neural Image Caption Generator". 
It follows the basic encoder-decoder architecture. 

The encoder consists of a ResNet backbone with a dense layer implanted on top of it. I sticked with Udacity's default choice here. The output is a feature vector which is the initial input into decoder.

The heart of the decoder is a single lstm cell which takes a word vector as input. The output of the lstm is fed through a dense layer which outputs a score distribution for the next generated word. The distribution is converted to proper probabilities via the softmax function. In inference mode, new word indices are sampled from these probabilities. Given a new word index, either from sampling or as part of a training sequence, it is converted by an embedding layer into a new input for the lstm. The size of the word vector matches the feature vector from the encoder. Thus subsequently generated word vectors are compatible with the initial input from the encoder.

Parameter choice:

* batch_size: Sticked to the number from 1_Preliminaries ...
* vocab_threshold: From the paper.
* embed_size & hidden_size: From the paper. Looks like the used the same size for both.
* num_epochs: Sticked to the suggested count.


### (Optional) Task #2

Note that we have provided a recommended image transform `transform_train` for pre-processing the training images, but you are welcome (and encouraged!) to modify it as you wish.  When modifying this transform, keep in mind that:
- the images in the dataset have varying heights and widths, and 
- if using a pre-trained model, you must perform the corresponding appropriate normalization.

### Question 2

**Question:** How did you select the transform in `transform_train`?  If you left the transform at its provided value, why do you think that it is a good choice for your CNN architecture?

**Answer:** I left it as provided. It checks all marks for a sensible transform:

* The image size of 224 pixels is commonly used for image classification. The ResNet backbone was probably trained on it. So it should not be too bad. However, since the resnet has a global average pooling layer at the end, it would be possible to use different sizes, I think.
* Doing a random crop is a simple way to do data augmentation which can help with overfitting, and good practice.
* Same with flipping.
* The normalization should match the normalization that was used during the training of the backbone. I trust that the provided values are sensible in this regard.
* One could do more, e.g. color augmentation as described in the implementation section of the ResNet paper (https://arxiv.org/pdf/1512.03385.pdf). But since I don't have the time to do ablation experiments I might as well keep things simple and not do more.

### Task #3

Next, you will specify a Python list containing the learnable parameters of the model.  For instance, if you decide to make all weights in the decoder trainable, but only want to train the weights in the embedding layer of the encoder, then you should set `params` to something like:
```
params = list(decoder.parameters()) + list(encoder.embed.parameters()) 
```

### Question 3

**Question:** How did you select the trainable parameters of your architecture?  Why do you think this is a good choice?

**Answer:** I only trained the parameters which are not pretrained already. It is a good choice according to the authors of the captioning paper "Show and Tell: A Neural Image Caption Generator". They remarked that training the  CNN weights had a negative impact on their results!

### Task #4

Finally, you will select an [optimizer](http://pytorch.org/docs/master/optim.html#torch.optim.Optimizer).

### Question 4

**Question:** How did you select the optimizer used to train your model?

**Answer:** I just picked my default. The Adam optimizer. It seems to be good for most purposes. In my experience it is not very sensitive to the learning rate. Something like 1e-4 often works fine. It did so in this case, albeit probably not optimally. I did not bother changing it since the loss was steadily decreasing.

In [1]:
import torch
import torch.nn as nn
from torchvision import transforms
import sys
sys.path.append('/opt/cocoapi/PythonAPI')
from pycocotools.coco import COCO
from data_loader import get_loader
from model import EncoderCNN, DecoderRNN
import math
import itertools

## TODO #1: Select appropriate values for the Python variables below.
batch_size = 10          # batch size
vocab_threshold = 5        # minimum word count threshold
vocab_from_file = True    # if True, load existing vocab file
embed_size = 512           # dimensionality of image and word embeddings
hidden_size = 512          # number of features in hidden state of the RNN decoder
num_epochs = 3             # number of training epochs
save_every = 1             # determines frequency of saving model weights
print_every = 100          # determines window for printing average loss
log_file = 'training_log.txt'       # name of file with saved training loss and perplexity

# (Optional) TODO #2: Amend the image transform below.
transform_train = transforms.Compose([ 
    transforms.Resize(256),                          # smaller edge of image resized to 256
    transforms.RandomCrop(224),                      # get 224x224 crop from random location
    transforms.RandomHorizontalFlip(),               # horizontally flip image with probability=0.5
    transforms.ToTensor(),                           # convert the PIL Image to a tensor
    transforms.Normalize((0.485, 0.456, 0.406),      # normalize image for pre-trained model
                         (0.229, 0.224, 0.225))])

# Build data loader.
data_loader = get_loader(transform=transform_train,
                         mode='train',
                         batch_size=batch_size,
                         vocab_threshold=vocab_threshold,
                         vocab_from_file=vocab_from_file)

# The size of the vocabulary.
vocab_size = len(data_loader.dataset.vocab)
#vocab_size = 1000

# Initialize the encoder and decoder. 
encoder = EncoderCNN(embed_size)
decoder = DecoderRNN(embed_size, hidden_size, vocab_size)

# Move models to GPU if CUDA is available. 
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
encoder.to(device)
decoder.to(device)

# Define the loss function. 
criterion = nn.CrossEntropyLoss().cuda() if torch.cuda.is_available() else nn.CrossEntropyLoss()

# TODO #3: Specify the learnable parameters of the model.
params = itertools.chain(
    (p for p in encoder.parameters() if p.requires_grad), 
    decoder.parameters())

# TODO #4: Define the optimizer.
optimizer = torch.optim.Adam(params, lr=1.e-4)

# Set the total number of training steps per epoch.
total_step = math.ceil(len(data_loader.dataset.caption_lengths) / data_loader.batch_sampler.batch_size)

Vocabulary successfully loaded from vocab.pkl file!
loading annotations into memory...
Done (t=0.87s)
creating index...


  0%|          | 806/414113 [00:00<01:48, 3825.12it/s]

index created!
Obtaining caption lengths...


100%|██████████| 414113/414113 [01:32<00:00, 4469.77it/s]


<a id='step2'></a>
## Step 2: Train your Model

Once you have executed the code cell in **Step 1**, the training procedure below should run without issue.  

It is completely fine to leave the code cell below as-is without modifications to train your model.  However, if you would like to modify the code used to train the model below, you must ensure that your changes are easily parsed by your reviewer.  In other words, make sure to provide appropriate comments to describe how your code works!  

You may find it useful to load saved weights to resume training.  In that case, note the names of the files containing the encoder and decoder weights that you'd like to load (`encoder_file` and `decoder_file`).  Then you can load the weights by using the lines below:

```python
# Load pre-trained weights before resuming training.
encoder.load_state_dict(torch.load(os.path.join('./models', encoder_file)))
decoder.load_state_dict(torch.load(os.path.join('./models', decoder_file)))
```

While trying out parameters, make sure to take extensive notes and record the settings that you used in your various training runs.  In particular, you don't want to encounter a situation where you've trained a model for several hours but can't remember what settings you used :).

### A Note on Tuning Hyperparameters

To figure out how well your model is doing, you can look at how the training loss and perplexity evolve during training - and for the purposes of this project, you are encouraged to amend the hyperparameters based on this information.  

However, this will not tell you if your model is overfitting to the training data, and, unfortunately, overfitting is a problem that is commonly encountered when training image captioning models.  

For this project, you need not worry about overfitting. **This project does not have strict requirements regarding the performance of your model**, and you just need to demonstrate that your model has learned **_something_** when you generate captions on the test data.  For now, we strongly encourage you to train your model for the suggested 3 epochs without worrying about performance; then, you should immediately transition to the next notebook in the sequence (**3_Inference.ipynb**) to see how your model performs on the test data.  If your model needs to be changed, you can come back to this notebook, amend hyperparameters (if necessary), and re-train the model.

That said, if you would like to go above and beyond in this project, you can read about some approaches to minimizing overfitting in section 4.3.1 of [this paper](http://ieeexplore.ieee.org/stamp/stamp.jsp?arnumber=7505636).  In the next (optional) step of this notebook, we provide some guidance for assessing the performance on the validation dataset.

In [ ]:
import torch.utils.data as data
import numpy as np
import os
import requests
import time

# Open the training log file.
f = open(log_file, 'w')

old_time = time.time()
response = requests.request("GET", 
                            "http://metadata.google.internal/computeMetadata/v1/instance/attributes/keep_alive_token", 
                            headers={"Metadata-Flavor":"Google"})

for epoch in range(1, num_epochs+1):
    
    for i_step in range(1, total_step+1):
        
        if time.time() - old_time > 60:
            old_time = time.time()
            requests.request("POST", 
                             "https://nebula.udacity.com/api/v1/remote/keep-alive", 
                             headers={'Authorization': "STAR " + response.text})
        
        # Randomly sample a caption length, and sample indices with that length.
        indices = data_loader.dataset.get_train_indices()
        # Create and assign a batch sampler to retrieve a batch with the sampled indices.
        new_sampler = data.sampler.SubsetRandomSampler(indices=indices)
        data_loader.batch_sampler.sampler = new_sampler
        
        # Obtain the batch.
        images, captions = next(iter(data_loader))

        # Move batch of images and captions to GPU if CUDA is available.
        images = images.to(device)
        captions = captions.to(device)
        
        # Zero the gradients.
        decoder.zero_grad()
        encoder.zero_grad()
        
        # Pass the inputs through the CNN-RNN model.
        features = encoder(images)
        outputs = decoder(features, captions)
        
        # Calculate the batch loss.
        loss = criterion(outputs.view(-1, vocab_size), captions.view(-1))
        
        # Backward pass.
        loss.backward()
        
        # Update the parameters in the optimizer.
        optimizer.step()
            
        # Get training statistics.
        stats = 'Epoch [%d/%d], Step [%d/%d], Loss: %.4f, Perplexity: %5.4f' % (epoch, num_epochs, i_step, total_step, loss.item(), np.exp(loss.item()))
        
        # Print training statistics (on same line).
        print('\r' + stats, end="")
        sys.stdout.flush()
        
        # Print training statistics to file.
        f.write(stats + '\n')
        f.flush()
        
        # Print training statistics (on different line).
        if i_step % print_every == 0:
            print('\r' + stats)
            
    # Save the weights.
    if epoch % save_every == 0:
        torch.save(decoder.state_dict(), os.path.join('./models', 'decoder-%d.pkl' % epoch))
        torch.save(encoder.state_dict(), os.path.join('./models', 'encoder-%d.pkl' % epoch))

# Close the training log file.
f.close()

Epoch [1/3], Step [100/41412], Loss: 4.8684, Perplexity: 130.1107
Epoch [1/3], Step [200/41412], Loss: 4.2609, Perplexity: 70.87338
Epoch [1/3], Step [300/41412], Loss: 4.0605, Perplexity: 58.00278
Epoch [1/3], Step [400/41412], Loss: 4.1995, Perplexity: 66.65582
Epoch [1/3], Step [500/41412], Loss: 4.0027, Perplexity: 54.74687
Epoch [1/3], Step [600/41412], Loss: 3.8690, Perplexity: 47.89244
Epoch [1/3], Step [700/41412], Loss: 3.6313, Perplexity: 37.76212
Epoch [1/3], Step [800/41412], Loss: 3.6163, Perplexity: 37.19894
Epoch [1/3], Step [900/41412], Loss: 4.0417, Perplexity: 56.92577
Epoch [1/3], Step [1000/41412], Loss: 3.8701, Perplexity: 47.9456
Epoch [1/3], Step [1100/41412], Loss: 3.9982, Perplexity: 54.49883
Epoch [1/3], Step [1200/41412], Loss: 3.8118, Perplexity: 45.23164
Epoch [1/3], Step [1300/41412], Loss: 3.1942, Perplexity: 24.39142
Epoch [1/3], Step [1400/41412], Loss: 3.8697, Perplexity: 47.92911
Epoch [1/3], Step [1500/41412], Loss: 3.9907, Perplexity: 54.09142
Epoch

Epoch [1/3], Step [24600/41412], Loss: 2.2356, Perplexity: 9.35228
Epoch [1/3], Step [24700/41412], Loss: 2.0933, Perplexity: 8.11149
Epoch [1/3], Step [24800/41412], Loss: 2.0650, Perplexity: 7.88533
Epoch [1/3], Step [24900/41412], Loss: 2.2593, Perplexity: 9.57647
Epoch [1/3], Step [25000/41412], Loss: 3.3767, Perplexity: 29.2740
Epoch [1/3], Step [25100/41412], Loss: 2.4643, Perplexity: 11.7548
Epoch [1/3], Step [25200/41412], Loss: 2.1507, Perplexity: 8.59089
Epoch [1/3], Step [25300/41412], Loss: 2.2472, Perplexity: 9.46160
Epoch [1/3], Step [25400/41412], Loss: 2.0458, Perplexity: 7.73550
Epoch [1/3], Step [25500/41412], Loss: 2.2472, Perplexity: 9.46101
Epoch [1/3], Step [25600/41412], Loss: 2.8139, Perplexity: 16.6756
Epoch [1/3], Step [25700/41412], Loss: 2.1131, Perplexity: 8.27405
Epoch [1/3], Step [25800/41412], Loss: 2.2478, Perplexity: 9.46698
Epoch [1/3], Step [25900/41412], Loss: 2.6886, Perplexity: 14.7112
Epoch [1/3], Step [26000/41412], Loss: 3.3732, Perplexity: 29.

Epoch [2/3], Step [7700/41412], Loss: 2.2932, Perplexity: 9.90697
Epoch [2/3], Step [7800/41412], Loss: 1.9202, Perplexity: 6.82211
Epoch [2/3], Step [7900/41412], Loss: 2.5339, Perplexity: 12.6021
Epoch [2/3], Step [8000/41412], Loss: 2.7616, Perplexity: 15.82506
Epoch [2/3], Step [8100/41412], Loss: 2.2728, Perplexity: 9.70649
Epoch [2/3], Step [8200/41412], Loss: 2.1416, Perplexity: 8.51287
Epoch [2/3], Step [8300/41412], Loss: 2.3781, Perplexity: 10.7843
Epoch [2/3], Step [8400/41412], Loss: 2.0399, Perplexity: 7.69022
Epoch [2/3], Step [8500/41412], Loss: 2.3766, Perplexity: 10.7686
Epoch [2/3], Step [8600/41412], Loss: 1.8601, Perplexity: 6.42412
Epoch [2/3], Step [8700/41412], Loss: 1.7294, Perplexity: 5.63743
Epoch [2/3], Step [8800/41412], Loss: 2.3416, Perplexity: 10.3983
Epoch [2/3], Step [8900/41412], Loss: 2.5923, Perplexity: 13.3603
Epoch [2/3], Step [9000/41412], Loss: 2.3615, Perplexity: 10.6072
Epoch [2/3], Step [9100/41412], Loss: 2.0707, Perplexity: 7.93046
Epoch [2/

Epoch [2/3], Step [32200/41412], Loss: 2.4381, Perplexity: 11.4514
Epoch [2/3], Step [32300/41412], Loss: 2.5122, Perplexity: 12.3323
Epoch [2/3], Step [32400/41412], Loss: 2.5324, Perplexity: 12.5842
Epoch [2/3], Step [32500/41412], Loss: 1.8249, Perplexity: 6.20250
Epoch [2/3], Step [32600/41412], Loss: 2.7723, Perplexity: 15.9954
Epoch [2/3], Step [32700/41412], Loss: 2.0026, Perplexity: 7.40830
Epoch [2/3], Step [32800/41412], Loss: 1.5855, Perplexity: 4.88188
Epoch [2/3], Step [32900/41412], Loss: 2.2291, Perplexity: 9.29145
Epoch [2/3], Step [33000/41412], Loss: 1.8088, Perplexity: 6.10340
Epoch [2/3], Step [33100/41412], Loss: 2.2380, Perplexity: 9.37485
Epoch [2/3], Step [33200/41412], Loss: 2.2637, Perplexity: 9.61834
Epoch [2/3], Step [33300/41412], Loss: 2.2063, Perplexity: 9.08212
Epoch [2/3], Step [33400/41412], Loss: 2.2688, Perplexity: 9.66829
Epoch [2/3], Step [33500/41412], Loss: 2.7743, Perplexity: 16.0280
Epoch [2/3], Step [33600/41412], Loss: 2.0546, Perplexity: 7.8

Epoch [3/3], Step [15300/41412], Loss: 1.8165, Perplexity: 6.15063
Epoch [3/3], Step [15400/41412], Loss: 2.2938, Perplexity: 9.91213
Epoch [3/3], Step [15500/41412], Loss: 2.0379, Perplexity: 7.67468
Epoch [3/3], Step [15600/41412], Loss: 1.9168, Perplexity: 6.79939
Epoch [3/3], Step [15700/41412], Loss: 1.7888, Perplexity: 5.98211
Epoch [3/3], Step [15800/41412], Loss: 2.0532, Perplexity: 7.79319
Epoch [3/3], Step [15900/41412], Loss: 1.7223, Perplexity: 5.59774
Epoch [3/3], Step [16000/41412], Loss: 1.8938, Perplexity: 6.64444
Epoch [3/3], Step [16100/41412], Loss: 1.6484, Perplexity: 5.19869
Epoch [3/3], Step [16200/41412], Loss: 2.3036, Perplexity: 10.0099
Epoch [3/3], Step [16300/41412], Loss: 2.0540, Perplexity: 7.79947
Epoch [3/3], Step [16400/41412], Loss: 2.4898, Perplexity: 12.0590
Epoch [3/3], Step [16500/41412], Loss: 1.8555, Perplexity: 6.39493
Epoch [3/3], Step [16600/41412], Loss: 2.8601, Perplexity: 17.4641
Epoch [3/3], Step [16700/41412], Loss: 1.8767, Perplexity: 6.5

In [1]:
%ls

0_Dataset.ipynb                               data_loader.py
0_Dataset-zh.ipynb                            filelist.txt
1_Preliminaries.ipynb                         images/
1_Preliminaries-zh.ipynb                      model.py
2_Training.ipynb                              models/
2_Training-zh.ipynb                           __pycache__/
3_Inference.ipynb                             training_log.txt
3_Inference-zh.ipynb                          vocab.pkl
4_Zip Your Project Files and Submit.ipynb     vocabulary.py
4_Zip Your Project Files and Submit-zh.ipynb


In [2]:
%ls models/

decoder-1.pkl  decoder-3.pkl  encoder-2.pkl
decoder-2.pkl  encoder-1.pkl  encoder-3.pkl


In [ ]:
%cat training_log.txt

Epoch [1/3], Step [1/41412], Loss: 9.1051, Perplexity: 9000.6493
Epoch [1/3], Step [2/41412], Loss: 9.0855, Perplexity: 8826.5273
Epoch [1/3], Step [3/41412], Loss: 9.0553, Perplexity: 8564.1307
Epoch [1/3], Step [4/41412], Loss: 9.0461, Perplexity: 8485.3289
Epoch [1/3], Step [5/41412], Loss: 9.0199, Perplexity: 8265.6614
Epoch [1/3], Step [6/41412], Loss: 8.9969, Perplexity: 8077.9230
Epoch [1/3], Step [7/41412], Loss: 8.9808, Perplexity: 7949.1984
Epoch [1/3], Step [8/41412], Loss: 8.9240, Perplexity: 7510.2470
Epoch [1/3], Step [9/41412], Loss: 8.9354, Perplexity: 7596.4350
Epoch [1/3], Step [10/41412], Loss: 8.8800, Perplexity: 7186.6682
Epoch [1/3], Step [11/41412], Loss: 8.8654, Perplexity: 7082.5065
Epoch [1/3], Step [12/41412], Loss: 8.8816, Perplexity: 7198.6105
Epoch [1/3], Step [13/41412], Loss: 8.8921, Perplexity: 7274.1428
Epoch [1/3], Step [14/41412], Loss: 8.7936, Perplexity: 6592.1661
Epoch [1/3], Step [15/41412], Loss: 8.7840, Perplexity: 6529.1613
Epoch [1/3], Step [

Epoch [1/3], Step [5398/41412], Loss: 3.0800, Perplexity: 21.7586
Epoch [1/3], Step [5399/41412], Loss: 3.0951, Perplexity: 22.0888
Epoch [1/3], Step [5400/41412], Loss: 3.1134, Perplexity: 22.4971
Epoch [1/3], Step [5401/41412], Loss: 3.3447, Perplexity: 28.3522
Epoch [1/3], Step [5402/41412], Loss: 3.1111, Perplexity: 22.4447
Epoch [1/3], Step [5403/41412], Loss: 2.6704, Perplexity: 14.4450
Epoch [1/3], Step [5404/41412], Loss: 3.0627, Perplexity: 21.3846
Epoch [1/3], Step [5405/41412], Loss: 2.8152, Perplexity: 16.6960
Epoch [1/3], Step [5406/41412], Loss: 3.2335, Perplexity: 25.3693
Epoch [1/3], Step [5407/41412], Loss: 3.0036, Perplexity: 20.1578
Epoch [1/3], Step [5408/41412], Loss: 3.1482, Perplexity: 23.2932
Epoch [1/3], Step [5409/41412], Loss: 3.3553, Perplexity: 28.6554
Epoch [1/3], Step [5410/41412], Loss: 3.7109, Perplexity: 40.8914
Epoch [1/3], Step [5411/41412], Loss: 2.9574, Perplexity: 19.2488
Epoch [1/3], Step [5412/41412], Loss: 2.8894, Perplexity: 17.9834
Epoch [1/3

Epoch [1/3], Step [9265/41412], Loss: 2.1774, Perplexity: 8.8233
Epoch [1/3], Step [9266/41412], Loss: 3.0358, Perplexity: 20.8183
Epoch [1/3], Step [9267/41412], Loss: 2.6941, Perplexity: 14.7919
Epoch [1/3], Step [9268/41412], Loss: 2.8169, Perplexity: 16.7242
Epoch [1/3], Step [9269/41412], Loss: 2.8625, Perplexity: 17.5061
Epoch [1/3], Step [9270/41412], Loss: 2.9800, Perplexity: 19.6880
Epoch [1/3], Step [9271/41412], Loss: 2.6162, Perplexity: 13.6839
Epoch [1/3], Step [9272/41412], Loss: 2.7704, Perplexity: 15.9642
Epoch [1/3], Step [9273/41412], Loss: 2.4360, Perplexity: 11.4268
Epoch [1/3], Step [9274/41412], Loss: 2.0990, Perplexity: 8.1576
Epoch [1/3], Step [9275/41412], Loss: 2.9989, Perplexity: 20.0627
Epoch [1/3], Step [9276/41412], Loss: 2.4715, Perplexity: 11.8402
Epoch [1/3], Step [9277/41412], Loss: 2.9947, Perplexity: 19.9800
Epoch [1/3], Step [9278/41412], Loss: 2.8340, Perplexity: 17.0135
Epoch [1/3], Step [9279/41412], Loss: 3.4020, Perplexity: 30.0254
Epoch [1/3],

Epoch [1/3], Step [11718/41412], Loss: 3.3712, Perplexity: 29.1146
Epoch [1/3], Step [11719/41412], Loss: 1.9966, Perplexity: 7.3637
Epoch [1/3], Step [11720/41412], Loss: 2.6724, Perplexity: 14.4741
Epoch [1/3], Step [11721/41412], Loss: 2.6223, Perplexity: 13.7680
Epoch [1/3], Step [11722/41412], Loss: 2.2585, Perplexity: 9.5683
Epoch [1/3], Step [11723/41412], Loss: 2.4977, Perplexity: 12.1543
Epoch [1/3], Step [11724/41412], Loss: 2.7500, Perplexity: 15.6433
Epoch [1/3], Step [11725/41412], Loss: 2.7603, Perplexity: 15.8044
Epoch [1/3], Step [11726/41412], Loss: 2.8523, Perplexity: 17.3282
Epoch [1/3], Step [11727/41412], Loss: 3.0941, Perplexity: 22.0678
Epoch [1/3], Step [11728/41412], Loss: 3.0737, Perplexity: 21.6225
Epoch [1/3], Step [11729/41412], Loss: 2.4568, Perplexity: 11.6671
Epoch [1/3], Step [11730/41412], Loss: 2.4864, Perplexity: 12.0180
Epoch [1/3], Step [11731/41412], Loss: 2.7129, Perplexity: 15.0729
Epoch [1/3], Step [11732/41412], Loss: 3.3349, Perplexity: 28.07

Epoch [1/3], Step [14172/41412], Loss: 2.2266, Perplexity: 9.2681
Epoch [1/3], Step [14173/41412], Loss: 2.0431, Perplexity: 7.7147
Epoch [1/3], Step [14174/41412], Loss: 2.2892, Perplexity: 9.8669
Epoch [1/3], Step [14175/41412], Loss: 2.8049, Perplexity: 16.5253
Epoch [1/3], Step [14176/41412], Loss: 1.9055, Perplexity: 6.7227
Epoch [1/3], Step [14177/41412], Loss: 2.7376, Perplexity: 15.4495
Epoch [1/3], Step [14178/41412], Loss: 3.1313, Perplexity: 22.9043
Epoch [1/3], Step [14179/41412], Loss: 2.5358, Perplexity: 12.6266
Epoch [1/3], Step [14180/41412], Loss: 2.4014, Perplexity: 11.0383
Epoch [1/3], Step [14181/41412], Loss: 2.4860, Perplexity: 12.0134
Epoch [1/3], Step [14182/41412], Loss: 2.6705, Perplexity: 14.4469
Epoch [1/3], Step [14183/41412], Loss: 2.4098, Perplexity: 11.1321
Epoch [1/3], Step [14184/41412], Loss: 2.3884, Perplexity: 10.8956
Epoch [1/3], Step [14185/41412], Loss: 2.2807, Perplexity: 9.7834
Epoch [1/3], Step [14186/41412], Loss: 3.3838, Perplexity: 29.4833


...

Epoch [3/3], Step [821/41412], Loss: 1.9155, Perplexity: 6.7901
Epoch [3/3], Step [822/41412], Loss: 2.0653, Perplexity: 7.8880
Epoch [3/3], Step [823/41412], Loss: 2.2658, Perplexity: 9.6388
Epoch [3/3], Step [824/41412], Loss: 3.0479, Perplexity: 21.0715
Epoch [3/3], Step [825/41412], Loss: 2.3577, Perplexity: 10.5661
Epoch [3/3], Step [826/41412], Loss: 2.4108, Perplexity: 11.1430
Epoch [3/3], Step [827/41412], Loss: 1.9606, Perplexity: 7.1035
Epoch [3/3], Step [828/41412], Loss: 1.6357, Perplexity: 5.1332
Epoch [3/3], Step [829/41412], Loss: 1.9118, Perplexity: 6.7651
Epoch [3/3], Step [830/41412], Loss: 2.1683, Perplexity: 8.7430
Epoch [3/3], Step [831/41412], Loss: 2.1338, Perplexity: 8.4470
Epoch [3/3], Step [832/41412], Loss: 1.8239, Perplexity: 6.1960
Epoch [3/3], Step [833/41412], Loss: 2.3764, Perplexity: 10.7659
Epoch [3/3], Step [834/41412], Loss: 1.8616, Perplexity: 6.4339
Epoch [3/3], Step [835/41412], Loss: 1.8965, Perplexity: 6.6627
Epoch [3/3], Step [836/41412], Loss:

Epoch [3/3], Step [1376/41412], Loss: 2.0954, Perplexity: 8.1288
Epoch [3/3], Step [1377/41412], Loss: 2.1679, Perplexity: 8.7395
Epoch [3/3], Step [1378/41412], Loss: 1.6233, Perplexity: 5.0696
Epoch [3/3], Step [1379/41412], Loss: 2.1775, Perplexity: 8.8243
Epoch [3/3], Step [1380/41412], Loss: 1.8290, Perplexity: 6.2274
Epoch [3/3], Step [1381/41412], Loss: 1.9645, Perplexity: 7.1316
Epoch [3/3], Step [1382/41412], Loss: 2.2695, Perplexity: 9.6745
Epoch [3/3], Step [1383/41412], Loss: 2.2672, Perplexity: 9.6525
Epoch [3/3], Step [1384/41412], Loss: 2.2828, Perplexity: 9.8039
Epoch [3/3], Step [1385/41412], Loss: 2.4914, Perplexity: 12.0782
Epoch [3/3], Step [1386/41412], Loss: 2.4484, Perplexity: 11.5697
Epoch [3/3], Step [1387/41412], Loss: 3.0128, Perplexity: 20.3436
Epoch [3/3], Step [1388/41412], Loss: 1.8212, Perplexity: 6.1791
Epoch [3/3], Step [1389/41412], Loss: 2.6330, Perplexity: 13.9153
Epoch [3/3], Step [1390/41412], Loss: 1.8554, Perplexity: 6.3944
Epoch [3/3], Step [13

Epoch [3/3], Step [1862/41412], Loss: 2.0077, Perplexity: 7.4459
Epoch [3/3], Step [1863/41412], Loss: 1.8872, Perplexity: 6.6010
Epoch [3/3], Step [1864/41412], Loss: 2.1407, Perplexity: 8.5052
Epoch [3/3], Step [1865/41412], Loss: 2.3214, Perplexity: 10.1899
Epoch [3/3], Step [1866/41412], Loss: 3.6390, Perplexity: 38.0526
Epoch [3/3], Step [1867/41412], Loss: 2.5973, Perplexity: 13.4281
Epoch [3/3], Step [1868/41412], Loss: 2.8090, Perplexity: 16.5935
Epoch [3/3], Step [1869/41412], Loss: 1.8255, Perplexity: 6.2057
Epoch [3/3], Step [1870/41412], Loss: 1.5127, Perplexity: 4.5391
Epoch [3/3], Step [1871/41412], Loss: 2.0737, Perplexity: 7.9541
Epoch [3/3], Step [1872/41412], Loss: 1.8569, Perplexity: 6.4040
Epoch [3/3], Step [1873/41412], Loss: 2.3808, Perplexity: 10.8140
Epoch [3/3], Step [1874/41412], Loss: 2.4752, Perplexity: 11.8839
Epoch [3/3], Step [1875/41412], Loss: 2.7017, Perplexity: 14.9057
Epoch [3/3], Step [1876/41412], Loss: 2.1878, Perplexity: 8.9160
Epoch [3/3], Step 

Epoch [3/3], Step [2409/41412], Loss: 2.2642, Perplexity: 9.6236
Epoch [3/3], Step [2410/41412], Loss: 2.9352, Perplexity: 18.8257
Epoch [3/3], Step [2411/41412], Loss: 1.8768, Perplexity: 6.5324
Epoch [3/3], Step [2412/41412], Loss: 2.9416, Perplexity: 18.9463
Epoch [3/3], Step [2413/41412], Loss: 1.7815, Perplexity: 5.9388
Epoch [3/3], Step [2414/41412], Loss: 2.2111, Perplexity: 9.1254
Epoch [3/3], Step [2415/41412], Loss: 1.9694, Perplexity: 7.1665
Epoch [3/3], Step [2416/41412], Loss: 2.0262, Perplexity: 7.5854
Epoch [3/3], Step [2417/41412], Loss: 2.7087, Perplexity: 15.0100
Epoch [3/3], Step [2418/41412], Loss: 2.1320, Perplexity: 8.4317
Epoch [3/3], Step [2419/41412], Loss: 1.8636, Perplexity: 6.4471
Epoch [3/3], Step [2420/41412], Loss: 1.9582, Perplexity: 7.0868
Epoch [3/3], Step [2421/41412], Loss: 1.8066, Perplexity: 6.0896
Epoch [3/3], Step [2422/41412], Loss: 1.8749, Perplexity: 6.5200
Epoch [3/3], Step [2423/41412], Loss: 2.0061, Perplexity: 7.4346
Epoch [3/3], Step [242

Epoch [3/3], Step [3017/41412], Loss: 1.5862, Perplexity: 4.8852
Epoch [3/3], Step [3018/41412], Loss: 2.5161, Perplexity: 12.3800
Epoch [3/3], Step [3019/41412], Loss: 2.2117, Perplexity: 9.1316
Epoch [3/3], Step [3020/41412], Loss: 2.1545, Perplexity: 8.6234
Epoch [3/3], Step [3021/41412], Loss: 2.2016, Perplexity: 9.0398
Epoch [3/3], Step [3022/41412], Loss: 2.0718, Perplexity: 7.9389
Epoch [3/3], Step [3023/41412], Loss: 2.2233, Perplexity: 9.2377
Epoch [3/3], Step [3024/41412], Loss: 2.3611, Perplexity: 10.6028
Epoch [3/3], Step [3025/41412], Loss: 1.9741, Perplexity: 7.2001
Epoch [3/3], Step [3026/41412], Loss: 2.3370, Perplexity: 10.3501
Epoch [3/3], Step [3027/41412], Loss: 2.4818, Perplexity: 11.9629
Epoch [3/3], Step [3028/41412], Loss: 2.2658, Perplexity: 9.6393
Epoch [3/3], Step [3029/41412], Loss: 2.0890, Perplexity: 8.0768
Epoch [3/3], Step [3030/41412], Loss: 1.7836, Perplexity: 5.9512
Epoch [3/3], Step [3031/41412], Loss: 2.1636, Perplexity: 8.7024
Epoch [3/3], Step [30

<a id='step3'></a>
## Step 3: (Optional) Validate your Model

To assess potential overfitting, one approach is to assess performance on a validation set.  If you decide to do this **optional** task, you are required to first complete all of the steps in the next notebook in the sequence (**3_Inference.ipynb**); as part of that notebook, you will write and test code (specifically, the `sample` method in the `DecoderRNN` class) that uses your RNN decoder to generate captions.  That code will prove incredibly useful here. 

If you decide to validate your model, please do not edit the data loader in **data_loader.py**.  Instead, create a new file named **data_loader_val.py** containing the code for obtaining the data loader for the validation data.  You can access:
- the validation images at filepath `'/opt/cocoapi/images/train2014/'`, and
- the validation image caption annotation file at filepath `'/opt/cocoapi/annotations/captions_val2014.json'`.

The suggested approach to validating your model involves creating a json file such as [this one](https://github.com/cocodataset/cocoapi/blob/master/results/captions_val2014_fakecap_results.json) containing your model's predicted captions for the validation images.  Then, you can write your own script or use one that you [find online](https://github.com/tylin/coco-caption) to calculate the BLEU score of your model.  You can read more about the BLEU score, along with other evaluation metrics (such as TEOR and Cider) in section 4.1 of [this paper](https://arxiv.org/pdf/1411.4555.pdf).  For more information about how to use the annotation file, check out the [website](http://cocodataset.org/#download) for the COCO dataset.

In [ ]:
# (Optional) TODO: Validate your model.